In [ ]:
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt
import laspy

figsize = (16, 9)

# Load LAS files data

In [ ]:
def find_las(path):
    print(path)
    las = list()
    
    if path.is_dir():
        for child in path.iterdir():
            las.extend(find_las(child))
    
    if path.is_file() and path.suffix == '.las':
        las.append(path)
    
    return las

In [ ]:
files = ['../Data/lidar/C1/272056_3289689.las',
         '../Data/lidar/C1/272652_3289689.las',
         '../Data/lidar/C1/273248_3289689.las',
         '../Data/lidar/C1/273844_3289689.las']

folder = Path('../Data/lidar/')
files  = find_las(folder)

xdata = list()
ydata = list()
idata = list()

for file in files:
    infile = laspy.file.File(file)
    print('file: {}, point count: {}'.format(file, infile.header.get_count()))
    xdata.append(infile.x)
    ydata.append(infile.y)
    idata.append(infile.intensity)
    
data = np.array((np.concatenate(xdata), np.concatenate(ydata), np.concatenate(idata))).T
data.shape

## Display a 2D hist

In [ ]:
resolution = 2
ground_size = np.array((data[:,0].max() - data[:,0].min(), data[:,1].max() - data[:,1].min()))
display(ground_size)

bins = ground_size / resolution

In [ ]:
plt.figure(figsize=figsize)
hist, xedges, yedges = np.histogram2d(data[:,0], data[:,1], bins=bins)
plt.imshow(hist.T, origin='lower', extent=[xedges[0], xedges[-1], yedges[0], yedges[-1]])
plt.show()

In [ ]:
plt.imsave('../Res/hist.png', hist.T, origin='lower')

## Display intensity map

In [ ]:
plt.figure(figsize=figsize)
hist_i, xedges, yedges = np.histogram2d(data[:,0], data[:,1], bins=bins, weights=data[:,2])
plt.imshow(hist_i.T / hist.T, origin='lower', extent=[xedges[0], xedges[-1], yedges[0], yedges[-1]])
plt.show()

It seems that we have no data at this resolution. Should interpolate ?

### Better intensity display

In [ ]:
i = hist_i.T /  hist.T
f = np.logical_not(np.isnan(i))
plt.hist(i[f], bins=1000)
plt.show()

i[f].min(), i[f].max()

In [ ]:
imax_disp = 10000

idisp = i
idisp[i > imax_disp] = imax_disp

plt.figure(figsize=figsize)
plt.imshow(idisp, origin='lower', extent=[xedges[0], xedges[-1], yedges[0], yedges[-1]])
plt.show()

In [ ]:
plt.imsave('../Res/hist_int.png', idisp, origin='lower')

In [ ]:
plt.scatter(infile.x, infile.y)
plt.show()